In [0]:
import json
from urllib.request import urlretrieve
from collections import defaultdict
import pandas as pd
import numpy as np
import seaborn as sns
from matplotlib import pyplot as plt
import requests
from pyspark.sql import Row

## Create database

In [0]:
%sql 
CREATE DATABASE IF NOT EXISTS MILESTONE2WATER

#SHORTAGE DATA API

#### In this first section, the data is read in a list of dictionary records and converted to a Pandas dataframe and stored as CSV

- URL = https://data.ca.gov/dataset/household-water-supply-shortage-reporting-system-data/resource/1625f0d1-20c0-4059-ba59-b26f0ff3a1c3
- Click on Data API
- Copy Query example for request URL with limit and search terms
- The data can also be downloaded

In [0]:
#https://stackoverflow.com/questions/63650969/databricks-consuming-rest-api?rq=1# 

api_retrieve = requests.get('https://data.cnra.ca.gov/api/3/action/datastore_search?resource_id=e1fd9f48-a613-4567-8042-3d2e064d77c8&limit=9000').json()
#Create a list of records
data_shortage = api_retrieve['result']['records']
pd_df_shortage = pd.DataFrame(data_shortage)
pd_df_shortage.to_csv('/dbfs/FileStore/shortage.csv')



#df_shortage = spark.createDataFrame(Row(**row) for row in data_shortage)

### Get Well Completion data

In [0]:
well_completion_api = requests.get('https://data.cnra.ca.gov/api/3/action/datastore_search?resource_id=8da7b93b-4e69-495d-9caa-335691a1896b&limit=3200').json()
list_data_completion = well_completion_api['result']['records']

while well_completion_api['result']['records']:
    well_completion_api = requests.get('https://data.cnra.ca.gov'+well_completion_api['result']['_links']["next"]).json()
    list_data_completion.extend(well_completion_api['result']['records'])
#Create a list of records

pd_df_wellcompletion = pd.DataFrame(list_data_completion)
pd_df_wellcompletion.to_csv('/dbfs/FileStore/wellcompletion.csv')

### Get periodic ground water data

In [0]:
groundwater_request_api = requests.get('https://data.cnra.ca.gov/api/3/action/datastore_search?resource_id=bfa9f262-24a1-45bd-8dc8-138bc8107266&limit=4000').json()
list_data_groundwater = groundwater_request_api['result']['records']
while groundwater_request_api['result']['records']:
    groundwater_request_api = requests.get('https://data.cnra.ca.gov'+groundwater_request_api['result']['_links']["next"]).json()
    list_data_groundwater.extend(groundwater_request_api['result']['records'])
    
    
pd_df_groundwaterwellcompletion = pd.DataFrame(list_data_groundwater)
pd_df_groundwater.to_csv('/dbfs/FileStore/groundwater.csv')

### Get Station information

In [0]:
# stations data has the location info for the measurement wells
stations_location_api = requests.get('https://data.cnra.ca.gov/api/3/action/datastore_search?resource_id=af157380-fb42-4abf-b72a-6f9f98868077&limit=32000').json()
list_data_stations = stations_location_api['result']['records']

while stations_location_api['result']['records']:
    stations_location_api = requests.get('https://data.cnra.ca.gov'+stations_location_api['result']['_links']["next"]).json()
    data_stations.extend(stations_location_api['result']['records'])
    
    
pd_df_station = pd.DataFrame(list_data_stations)
pd_df_station.to_csv('/dbfs/FileStore/station.csv')

### Convert a pandas dataframe to Spark with infer schema


- spark_df = pandas_to_spark(pandas_df)

In [0]:
from pyspark.sql.types import *

# Auxiliar functions
def equivalent_type(f):
    if f == 'datetime64[ns]': return TimestampType()
    elif f == 'int64': return LongType()
    elif f == 'int32': return IntegerType()
    elif f == 'float64': return FloatType()
    else: return StringType()

def define_structure(string, format_type):
    try: typo = equivalent_type(format_type)
    except: typo = StringType()
    return StructField(string, typo)

# Given pandas dataframe, it will return a spark's dataframe.
def pandas_to_spark(pandas_df):
    columns = list(pandas_df.columns)
    types = list(pandas_df.dtypes)
    struct_list = []
    for column, typo in zip(columns, types): 
      struct_list.append(define_structure(column, typo))
    p_schema = StructType(struct_list)
    return sqlContext.createDataFrame(pandas_df, p_schema)

# Method 2
- Create a spark dataframe from JSON data.  Coalesce the data into one parquet file and store it. 
- Read the Parquet file back using Spark

In [0]:

api_retrieve = requests.get('https://data.cnra.ca.gov/api/3/action/datastore_search?resource_id=e1fd9f48-a613-4567-8042-3d2e064d77c8&limit=9000').json()
#Create a list of records
list_data_shortage = api_retrieve['result']['records']



df_shortage = spark.createDataFrame(Row(**row) for row in list_data_shortage)

df_shortage.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/shortage.csv")

--------------------------------------------------------------------------- 
 AnalysisException Traceback (most recent call last)
 <command-2018882991844899> in <module> 
 7 df_shortage = spark . createDataFrame ( Row ( ** row ) for row in list_data_shortage ) 
 8 
 ----> 9 df_shortage . coalesce ( 1 ) . write . format ( "com.databricks.spark.csv" ) . option ( "header" , "true" ) . save ( "dbfs:/FileStore/WaterWell/shortage.csv" ) 

 /databricks/spark/python/pyspark/sql/readwriter.py in save (self, path, format, mode, partitionBy, **options) 
 1134 self . _jwrite . save ( ) 
 1135 else : 
 -> 1136 self . _jwrite . save ( path ) 
 1137 
 1138 @ since ( 1.4 ) 

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 121 # Hide where the exception came from that shows a non-Pythonic 
 122 # JVM exception message. 
 --> 123 raise converted from None 
 124 else : 
 125 raise 

 AnalysisException : path dbfs:/FileStore/WaterWell/shortage.csv already exists.

Spark dataframe stored as CSV for well completion

In [0]:
sc.stop()
configura=SparkConf().set('spark.rpc.message.maxSize','1024')
sc=SparkContext.getOrCreate(conf=configura)
spark = SparkSession.builder.getOrCreate()

In [0]:
well_completion_api = requests.get('https://data.cnra.ca.gov/api/3/action/datastore_search?resource_id=8da7b93b-4e69-495d-9caa-335691a1896b&limit=4000').json()
list_data_wellcompletion = well_completion_api['result']['records']
#Create a list of records
while well_completion_api['result']['records']:
    well_completion_api = requests.get('https://data.cnra.ca.gov'+well_completion_api['result']['_links']["next"]).json()
    list_data_wellcompletion.extend(well_completion_api['result']['records'])


df_wellcompletion = spark.createDataFrame(Row(**row) for row in list_data_wellcompletion)



In [0]:
df_wellcompletion.count()

Out[6]: 1043032

In [0]:
df_wellcompletion.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/spark_df_wellcompletion.csv")

--------------------------------------------------------------------------- 
 Py4JJavaError Traceback (most recent call last)
 <command-2797995886664628> in <module> 
 ----> 1 df_wellcompletion . coalesce ( 1 ) . write . format ( "com.databricks.spark.csv" ) . option ( "header" , "true" ) . save ( "dbfs:/FileStore/WaterWell/spark_df_wellcompletion.csv" ) 

 /databricks/spark/python/pyspark/sql/readwriter.py in save (self, path, format, mode, partitionBy, **options) 
 1134 self . _jwrite . save ( ) 
 1135 else : 
 -> 1136 self . _jwrite . save ( path ) 
 1137 
 1138 @ since ( 1.4 ) 

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 115 def deco ( * a , ** kw ) : 
 116 try : 
 --> 117 return f ( * a , ** kw ) 
 118 except py4j . protocol . Py4JJavaError as e : 
 119 converted = convert_exception ( e . java_exception ) 

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/protocol.py in get_return_value (answer, gateway_client, target_id, name) 
 324 value = OUTPUT_CONVERTER [ type ] ( answer [ 2 : ] , gateway_client ) 
 325 if answer [ 1 ] == REFERENCE_TYPE : 
 --> 326 raise Py4JJavaError(
 327 "An error occurred while calling {0}{1}{2}.\n" . 
 328 format(target_id, ".", name), value)

 Py4JJavaError : An error occurred while calling o1579.save.
: org.apache.spark.SparkException: Job aborted.
	at org.apache.spark.sql.execution.datasources.FileFormatWriter$.write(FileFormatWriter.scala:307)
	at org.apache.spark.sql.execution.datasources.InsertIntoHadoopFsRelationCommand.run(InsertIntoHadoopFsRelationCommand.scala:194)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult$lzycompute(commands.scala:121)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.sideEffectResult(commands.scala:119)
	at org.apache.spark.sql.execution.command.DataWritingCommandExec.doExecute(commands.scala:144)
	at org.apache.spark.sql.execution.SparkPlan.$anonfun$execute$1(SparkPlan.scala:213)
	at org.apache.spark.sql.execution.SparkPlan.$anonfun$executeQuery$1(SparkPlan.scala:257)
	at org.apache.spark.rdd.RDDOperationScope$.withScope(RDDOperationScope.scala:165)
	at org.apache.spark.sql.execution.SparkPlan.executeQuery(SparkPlan.scala:253)
	at org.apache.spark.sql.execution.SparkPlan.execute(SparkPlan.scala:209)
	at org.apache.spark.sql.execution.QueryExecution.toRdd$lzycompute(QueryExecution.scala:167)
	at org.apache.spark.sql.execution.QueryExecution.toRdd(QueryExecution.scala:166)
	at org.apache.spark.sql.DataFrameWriter.$anonfun$runCommand$1(DataFrameWriter.scala:1079)
	at org.apache.spark.sql.execution.SQLExecution$.$anonfun$withCustomExecutionEnv$5(SQLExecution.scala:126)
	at org.apache.spark.sql.execution.SQLExecution$.withSQLConfPropagated(SQLExecution.scala:269)
	at org.apache.spark.sql.execution.SQLExecution$.$anonfun$withCustomExecutionEnv$1(SQLExecution.scala:104)
	at org.apache.spark.sql.SparkSession.withActive(SparkSession.scala:852)
	at org.apache.spark.sql.execution.SQLExecution$.withCustomExecutionEnv(SQLExecution.scala:77)
	at org.apache.spark.sql.execution.SQLExecution$.withNewExecutionId(SQLExecution.scala:219)
	at org.apache.spark.sql.DataFrameWriter.runCommand(DataFrameWriter.scala:1079)
	at org.apache.spark.sql.DataFrameWriter.saveToV1Source(DataFrameWriter.scala:468)
	at org.apache.spark.sql.DataFrameWriter.saveInternal(DataFrameWriter.scala:438)
	at org.apache.spark.sql.DataFrameWriter.save(DataFrameWriter.scala:303)
	at sun.reflect.NativeMethodAccessorImpl.invoke0(Native Method)
	at sun.reflect.NativeMethodAccessorImpl.invoke(NativeMethodAccessorImpl.java:62)
	at sun.reflect.DelegatingMethodAccessorImpl.invoke(DelegatingMethodAccessorImpl.java:43)
	at java.lang.reflect.Method.invoke(Method.

## Spark dataframe saved as CSV for groundwater

In [0]:
#Create a list of records

groundwater_request_api = requests.get('https://data.cnra.ca.gov/api/3/action/datastore_search?resource_id=bfa9f262-24a1-45bd-8dc8-138bc8107266&limit=4000').json()
list_data_groundwater = groundwater_request_api['result']['records']
while groundwater_request_api['result']['records']:
    groundwater_request_api = requests.get('https://data.cnra.ca.gov'+groundwater_request_api['result']['_links']["next"]).json()
    list_data_groundwater.extend(groundwater_request_api['result']['records'])
    
df_groundwater = spark.createDataFrame(Row(**row) for row in list_data_groundwater)
df_groundwater.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/groundwater.csv")    

## Spark dataframe saved as CSV for station

In [0]:
%sql
show tables in milestone2water

database tableName isTemporary milestone2water table_completion false milestone2water table_groundwater false milestone2water table_shortage false milestone2water table_station false

In [0]:
spark_df_station = spark.sql("""select * from milestone2water.table_station""")
spark_df_station.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/spark_df_station.csv")

In [0]:
spark_df_wellcompletion = spark.sql("""select * from milestone2water.table_completion""")
spark_df_wellcompletion.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/spark_df_wellcompletion.csv")


In [0]:
spark_df_groundwater = spark.sql("""select * from milestone2water.table_groundwater""")
spark_df_groundwater.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/spark_df_groundwater.csv")

In [0]:
spark_df_shortage = spark.sql("""select * from milestone2water.table_shortage""")
spark_df_shortage.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/spark_df_shortage.csv")

### Create the HTML, which when pasted in a new browser window will automatically download the file

From the URL of the notebook, pick the strings shown

**https://adb-8268979028189023.3.azuredatabricks.net/?o=8268979028189023**#notebook/2018882991844828/command/2018882991844900


insert the file name and part name of the one parquet file created (go to data tab->Create Table-> DBFS-> FileStore)


https://adb-8268979028189023.3.azuredatabricks.net/files/WaterWell/shortage.csv/part-00000-tid-4400703674217460447-3a2e9c38-2679-4e6d-b5d7-e1a54b2d65ab-2-1-c000.csv?o=8268979028189023

### Read the "part" dataframe generated CSV into spark dataframe

In [0]:
# Reading csv file
# File location and type
file_location = "/FileStore/WaterWell/shortage.csv"
file_type = "csv"

# CSV options
infer_schema = "false"
first_row_is_header = "true"
delimiter = ","

# The applied options are for CSV files. For other file types, these will be ignored.
df = spark.read.format(file_type) \
  .option("inferSchema", infer_schema) \
  .option("header", first_row_is_header) \
  .option("sep", delimiter) \
  .load(file_location)

display(df)

Well Depth StatusType Status Household Support Pump Rate Reduction Water Issues Shortage Type Was Issue Resolved? CREATE DATE Approximate Issue Start Date Measure Date Primary Usages Region LONGITUDE Well to Water Depth ID CITY Approximate Repair Cost County Report Date LATITUDE _id Additional Info 45' Outage Undefined null >45' null Dry well (groundwater) null 09/11/2015 07/07/2015 null Household Inland -120.884807 May, 2015 3102 Empire null Stanislaus 2015-09-11T00:00:00 37.657762 1 null 47' Outage Undefined null 44' null Dry well (groundwater) null 09/11/2015 07/27/2015 null Household Inland -120.71052 Sept. 2014 3103 Hickman null Stanislaus 2015-09-11T00:00:00 37.6310712 2 null 85' Outage Undefined null >85' null Dry well (groundwater) null 09/11/2015 08/01/2015 null Household Inland -120.816245 42220 3105 Denair null Stanislaus 2015-09-11T00:00:00 37.578196 3 null 110' Outage Undefined null UNK null Dry well (groundwater) null 09/11/2015 08/01/2015 null Household Inland -120.960309 UNK 3108 Ceres null Stanislaus 2015-09-11T00:00:00 37.60228 4 null null Outage Undefined null null null Dry well (groundwater) null 07/31/2015 null null Household Inland -120.910673 null 942 Oakdale null Stanislaus 2015-07-31T00:00:00 37.73886 66 null 65' Outage Undefined null 65' null Dry well (groundwater) null 09/11/2015 08/15/2015 null Household Inland -121.033522 65' on 8/15/15 3109 Newman null Stanislaus 2015-09-11T00:00:00 37.317443 5 null UNK Outage Undefined null UNK null Dry well (groundwater) null 09/11/2015 08/20/2015 null Household Inland -120.755139 UNK 3110 Waterford null Stanislaus 2015-09-11T00:00:00 37.6603629 6 null null Outage Undefined null null null Dry well (groundwater) null 09/11/2015 09/10/2015 null Household Inland -120.899061 null 3111 Modesto null Stanislaus 2015-09-11T00:00:00 37.678451 7 null null Outage Undefined null null null Dry well (groundwater) null 09/11/2015 09/08/2015 null Household Inland -120.9008227 null 3112 Empire null Stanislaus 2015-09-11T00:00:00 37.638741 8 null Original well - 355 ft, new well - 540 ft Resolved Resolved owner-occupied 75% Reduction in water pressure, lower flows.
 null null null null null null null null null null null null null null null null null null Reduction in water quality null null null null null null null null null null null null null null null null null null null null null null Well is catching air have to wait to be able to pump." New well drilled with poor water quality, water level still falling Yes, drilled replacement well.
 null null null null null null null null null null null null null null null null null null null Poor water quality" 09/19/2015 01/01/2013 09/19/2015 Combination of Household/Agriculture Southern -120.621761 280 ft - continuous measurement with Wellntel 3121 Templeton $25,000 San Luis Obispo 2015-09-19T00:00:00 35.544734 9 Many of our neighbors have drilled new wells into poor quality water or are trucking water for their homes. null null null null null null null Outage Outage owner-occupied null Well is dry (no longer producing water) Dry well (groundwater) No, getting water from our neighbors with a hose
 null null null null null null null null null null null null null null null null Paying monthly to neighbors null null null null null null null null null null null null null null null null null null null null null null No cannot afford to finance solutions." 09/22/2015 07/02/2012 null Household Southern -120.555413 null 3122 Paso Robles null San Luis Obispo 2015-09-22T00:00:00 35.624832 10 null null null null null null 360ft. Outage Outage owner-occupied It's no longer producing any water Well is dry (no longer producing water) Dry well (groundwater) No, trucking in water
 null null null null null null null null null null null null null null null null No cannot afford to finance solutions." 09/22/2015 06/01/2013 null Household Southern -120.555153 null 3123 Paso Robles null San Luis Obispo 2015-09-22T00:00:00 35.629448 11 null null null null n

In [0]:
# dbutils.fs.ls(f"dbfs:/FileStore/shortage.csv")
# dbutils.fs.rm(f"dbfs:/FileStore/WaterWell/shortage.csv", True)

#dbutils.fs.ls(f"dbfs:/FileStore/shortage.csv")
#dbutils.fs.rm(f"dbfs:/FileStore/WaterWell/wellcompletion.csv", True)
dbutils.fs.rm(f"dbfs:/FileStore/WaterWell/groundwater.csv", True)

Out[75]: True

In [0]:
#pandas_df = pd.read_csv('/dbfs/FileStore/shortage.csv', header='infer') 

### Check if you can read back the saved csv

In [0]:
pd_df_shortage.columns

Out[46]: Index(['Well Depth', 'StatusType', 'Status', 'Household Support',
 'Pump Rate Reduction', 'Water Issues', 'Shortage Type',
 'Was Issue Resolved?', 'CREATE DATE', 'Approximate Issue Start Date',
 'Measure Date', 'Primary Usages', 'Region', 'LONGITUDE',
 'Well to Water Depth', 'ID', 'CITY', 'Approximate Repair Cost',
 'County', 'Report Date', 'LATITUDE', '_id', 'Additional Info'],
 dtype='object')

In [0]:
#NOte https://databricks-prod-cloudfront.cloud.databricks.com/public/4027ec902e239c93eaaa8714f173bcfc/3137082781873852/3704545280501166/1264763342038607/latest.html
#In Databricks this global context object is available as sc for this purpose

from pyspark.sql import SQLContext
sqlContext = SQLContext(sc)
sqlContext 

Out[4]: <pyspark.sql.context.SQLContext at 0x7fbda7798490>

In [0]:
new_column_names = [col_name.replace(" ", "_") for col_name in df_shortage.columns ]
df_shortage =  df_shortage.toDF(*new_column_names)


In [0]:
#display(df_shortage)

Well_Depth StatusType Status Household_Support Pump_Rate_Reduction Water_Issues Shortage_Type Was_Issue_Resolved? CREATE_DATE Approximate_Issue_Start_Date Measure_Date Primary_Usages Region LONGITUDE Well_to_Water_Depth ID CITY Approximate_Repair_Cost County Report_Date LATITUDE _id Additional_Info 45' Outage Undefined null >45' null Dry well (groundwater) null 09/11/2015 07/07/2015 null Household Inland -120.884807 May, 2015 3102 Empire null Stanislaus 2015-09-11T00:00:00 37.657762 1 null 47' Outage Undefined null 44' null Dry well (groundwater) null 09/11/2015 07/27/2015 null Household Inland -120.71052 Sept. 2014 3103 Hickman null Stanislaus 2015-09-11T00:00:00 37.6310712 2 null 85' Outage Undefined null >85' null Dry well (groundwater) null 09/11/2015 08/01/2015 null Household Inland -120.816245 42220 3105 Denair null Stanislaus 2015-09-11T00:00:00 37.578196 3 null 110' Outage Undefined null UNK null Dry well (groundwater) null 09/11/2015 08/01/2015 null Household Inland -120.960309 UNK 3108 Ceres null Stanislaus 2015-09-11T00:00:00 37.60228 4 null null Outage Undefined null null 
 Dry well (groundwater) 
 07/31/2015 null null Household Inland -120.910673 null 942 Oakdale null Stanislaus 2015-07-31T00:00:00 37.73886 66 null 65' Outage Undefined null 65' null Dry well (groundwater) null 09/11/2015 08/15/2015 null Household Inland -121.033522 65' on 8/15/15 3109 Newman null Stanislaus 2015-09-11T00:00:00 37.317443 5 null UNK Outage Undefined null UNK null Dry well (groundwater) null 09/11/2015 08/20/2015 null Household Inland -120.755139 UNK 3110 Waterford null Stanislaus 2015-09-11T00:00:00 37.6603629 6 null null Outage Undefined null null null Dry well (groundwater) null 09/11/2015 09/10/2015 null Household Inland -120.899061 null 3111 Modesto null Stanislaus 2015-09-11T00:00:00 37.678451 7 null null Outage Undefined null null null Dry well (groundwater) null 09/11/2015 09/08/2015 null Household Inland -120.9008227 null 3112 Empire null Stanislaus 2015-09-11T00:00:00 37.638741 8 null Original well - 355 ft, new well - 540 ft Resolved Resolved owner-occupied 75% Reduction in water pressure, lower flows.
,Reduction in water quality
,Well is catching air, have to wait to be able to pump.
 New well drilled with poor water quality, water level still falling Yes, drilled replacement well.
,Poor water quality
 09/19/2015 01/01/2013 09/19/2015 Combination of Household/Agriculture Southern -120.621761 280 ft - continuous measurement with Wellntel 3121 Templeton $25,000 San Luis Obispo 2015-09-19T00:00:00 35.544734 9 Many of our neighbors have drilled new wells into poor quality water or are trucking water for their homes. null Outage Outage owner-occupied null Well is dry (no longer producing water)
 Dry well (groundwater) No, getting water from our neighbors with a hose
,Paying monthly to neighbors
,No, cannot afford to finance solutions.
 09/22/2015 07/02/2012 null Household Southern -120.555413 null 3122 Paso Robles null San Luis Obispo 2015-09-22T00:00:00 35.624832 10 null 360ft. Outage Outage owner-occupied It's no longer producing any water Well is dry (no longer producing water)
 Dry well (groundwater) No, trucking in water
,No, cannot afford to finance solutions.
 09/22/2015 06/01/2013 null Household Southern -120.555153 null 3123 Paso Robles null San Luis Obispo 2015-09-22T00:00:00 35.629448 11 null 300ft Outage Outage owner-occupied null Well is dry (no longer producing water)
 Dry well (groundwater) No, cannot afford to finance solutions.
 09/23/2015 09/05/2015 null Household Inland -121.039598 null 3124 Pilot Hill null El Dorado 2015-09-23T00:00:00 38.79552 12 We are looking at borrowing money to put in a storage tank to truck in water, although I am not sure how long we can afford this solution. It is roughly $270 for 1500 gallons of water to be delivered plus $5000 to put in a storage system. We just purchased the home and are also facing the cleaning of a former rat and mouse infestation in the home t

In [0]:
perm_table_name = "table_shortage"
df_shortage.write.format("parquet").saveAsTable(f"MILESTONE2WATER.{perm_table_name}")  

--------------------------------------------------------------------------- 
 AnalysisException Traceback (most recent call last)
 <command-760976672825033> in <module> 
 1 perm_table_name = "table_shortage" 
 ----> 2 df_shortage . write . format ( "parquet" ) . saveAsTable ( f"MILESTONE2WATER.{perm_table_name}" ) 

 /databricks/spark/python/pyspark/sql/readwriter.py in saveAsTable (self, name, format, mode, partitionBy, **options) 
 1183 if format is not None : 
 1184 self . format ( format ) 
 -> 1185 self . _jwrite . saveAsTable ( name ) 
 1186 
 1187 def json(self, path, mode=None, compression=None, dateFormat=None, timestampFormat=None,

 /databricks/spark/python/lib/py4j-0.10.9-src.zip/py4j/java_gateway.py in __call__ (self, *args) 
 1302 
 1303 answer = self . gateway_client . send_command ( command ) 
 -> 1304 return_value = get_return_value(
 1305 answer, self.gateway_client, self.target_id, self.name)
 1306 

 /databricks/spark/python/pyspark/sql/utils.py in deco (*a, **kw) 
 121 # Hide where the exception came from that shows a non-Pythonic 
 122 # JVM exception message. 
 --> 123 raise converted from None 
 124 else : 
 125 raise 

 AnalysisException : Table `MILESTONE2WATER`.`table_shortage` already exists.

In [0]:
%sql

SHOW TABLES IN milestone2water


database tableName isTemporary milestone2water table_completion false milestone2water table_shortage false

In [0]:
%sql
select * from milestone2water.table_shortage limit 3

Well_Depth StatusType Status Household_Support Pump_Rate_Reduction Water_Issues Shortage_Type Was_Issue_Resolved? CREATE_DATE Approximate_Issue_Start_Date Measure_Date Primary_Usages Region LONGITUDE Well_to_Water_Depth ID CITY Approximate_Repair_Cost County Report_Date LATITUDE _id Additional_Info null Outage Undefined null null Well is dry (no longer producing water)
 Dry well (groundwater) null 05/24/2021 04/06/2021 null Household Southern -120.61821 null 10230 TEMPLETON null San Luis Obispo 2021-05-24T00:00:00 35.50495 2830 null 166 Resolved Interim Solution owner-occupied Yes, about a 30-40% reduction Reduction in water pressure, lower flows.
 Dry well (groundwater) No, trucking in water
 05/25/2021 05/04/2021 05/18/2021 Household Inland -119.78637 148 10247 Lemoore null Kings 2021-05-25T00:00:00 36.30101 2831 null 200 Resolved Interim Solution owner-occupied It's no longer producing any water Well is dry (no longer producing water)
 Dry well (groundwater) No, trucking in water
 05/25/2021 05/14/2021 05/20/2021 Household Inland -119.995 200 10248 Madera null Madera 2021-05-25T00:00:00 37.05132 2832 null

In [0]:
perm_table_name = "table_completion"
df_wellcompletion.write.format("parquet").saveAsTable(f"MILESTONE2WATER.{perm_table_name}")  

In [0]:
%sql
show tables in MILESTONE2WATER

database tableName isTemporary milestone2water table_completion false milestone2water table_shortage false

In [0]:
%sql
SELECT COUNT(1) FROM MILESTONE2WATER.table_completion

count(1) 1043032

In [0]:
%sql
SELECT * FROM MILESTONE2WATER.table_completion LIMIT 1

DECIMALLATITUDE WORKFLOWSTATUS LLACCURACY PERMITDATE PUMPTESTLENGTH SECTION REGIONOFFICE DRILLINGMETHOD OTHEROBSERVATIONS WELLYIELDUNITOFMEASURE WELLLOCATION PERMITNUMBER TOTALDRAWDOWN VERTICALDATUM BOTTOMOFPERFORATEDINTERVAL GROUNDSURFACEELEVATION STATICWATERLEVEL RECORDTYPE DRILLERLICENSENUMBER FLUID TESTTYPE APN PLANNEDUSEFORMERUSE LOCALPERMITAGENCY TOPOFPERFORATEDINTERVAL WCRNUMBER TOTALDRILLDEPTH LEGACYLOGNUMBER ELEVATIONDETERMINATIONMETHOD ELEVATIONACCURACY DECIMALLONGITUDE METHODOFDETERMINATIONLL HORIZONTALDATUM TOWNSHIP DATEWORKENDED CITY TOTALCOMPLETEDDEPTH OWNERASSIGNEDWELLNUMBER COUNTYNAME RANGE BASELINEMERIDIAN RECEIVEDDATE DRILLERNAME WELLYIELD _id CASINGDIAMETER 34.12784 null Centroid of Section null null 36 DWR Southern Region Office Reverse Circulation null GPM EL CAMPO DR null null null 1080 null null WellCompletion/New/Production or Monitoring/NA 510011 Not Available at Conversion null null Water Supply Public LA County Department of Public Health, Department of Health Services, Drinking Water Program 610 WCR1776-006426 null 294182 null null -118.09132 Derived from TRS null 01N null Pasadena 1100 null Los Angeles 12W San Bernardino null McCalla Brothers Division McCalla Brothers Division of Layne Western 2270 260064 28

In [0]:
%sql
--DESCRIBE MILESTONE2WATER.table_completion; --WCRNUMBER
DESCRIBE MILESTONE2WATER.table_completion;--WCRNUMBER

col_name data_type comment DECIMALLATITUDE string null WORKFLOWSTATUS string null LLACCURACY string null PERMITDATE string null PUMPTESTLENGTH string null SECTION string null REGIONOFFICE string null DRILLINGMETHOD string null OTHEROBSERVATIONS string null WELLYIELDUNITOFMEASURE string null WELLLOCATION string null PERMITNUMBER string null TOTALDRAWDOWN string null VERTICALDATUM string null BOTTOMOFPERFORATEDINTERVAL string null GROUNDSURFACEELEVATION string null STATICWATERLEVEL string null RECORDTYPE string null DRILLERLICENSENUMBER string null FLUID string null TESTTYPE string null APN string null PLANNEDUSEFORMERUSE string null LOCALPERMITAGENCY string null TOPOFPERFORATEDINTERVAL string null WCRNUMBER string null TOTALDRILLDEPTH string null LEGACYLOGNUMBER string null ELEVATIONDETERMINATIONMETHOD string null ELEVATIONACCURACY string null DECIMALLONGITUDE string null METHODOFDETERMINATIONLL string null HORIZONTALDATUM string null TOWNSHIP string null DATEWORKENDED string null CITY string null TOTALCOMPLETEDDEPTH string null OWNERASSIGNEDWELLNUMBER string null COUNTYNAME string null RANGE string null BASELINEMERIDIAN string null RECEIVEDDATE string null DRILLERNAME string null WELLYIELD string null _id bigint null CASINGDIAMETER string null

## Conversion of spark dataframe to pandas is speeded up by the below (8 sec in this case)

In [0]:
# spark.conf.set("spark.sql.execution.arrow.enabled", "true")

# pd_df_wellcompletion = df_wellcompletion.toPandas()

In [0]:
#display(pd_df_wellcompletion)

DECIMALLATITUDE WORKFLOWSTATUS LLACCURACY PERMITDATE PUMPTESTLENGTH SECTION REGIONOFFICE DRILLINGMETHOD OTHEROBSERVATIONS WELLYIELDUNITOFMEASURE WELLLOCATION PERMITNUMBER TOTALDRAWDOWN VERTICALDATUM BOTTOMOFPERFORATEDINTERVAL GROUNDSURFACEELEVATION STATICWATERLEVEL RECORDTYPE DRILLERLICENSENUMBER FLUID TESTTYPE APN PLANNEDUSEFORMERUSE LOCALPERMITAGENCY TOPOFPERFORATEDINTERVAL WCRNUMBER TOTALDRILLDEPTH LEGACYLOGNUMBER ELEVATIONDETERMINATIONMETHOD ELEVATIONACCURACY DECIMALLONGITUDE METHODOFDETERMINATIONLL HORIZONTALDATUM TOWNSHIP DATEWORKENDED CITY TOTALCOMPLETEDDEPTH OWNERASSIGNEDWELLNUMBER COUNTYNAME RANGE BASELINEMERIDIAN RECEIVEDDATE DRILLERNAME WELLYIELD _id CASINGDIAMETER null null null null null NO NUMBER null null null null null null null null null null null WellCompletion/New/Production or Monitoring/NA null null null null null null null WCR0097017 null 095043 null null null null null null null null null null null null null null null null 1042952 null 37.532473 null >50 FT null null 03 DWR North Central Region Office null null null 41100 ROBERTS AVENUE 2015-0443 null null null null null WellCompletion/Destruction/NA/NA 938110 null null 525600185 null Alameda County Water District null WCR2015-006846 null E0289784 null null -121.956264 Derived from Address null 05S 10/29/2015 FREMONT 55 MW-10 Alameda 01W Mount Diablo null CASCADE DRILLING L P null 1 null 37.52371 null Unknown null null 02 DWR North Central Region Office SONIC null null 8333 ENTERPRISE DR. 2014-0063 null null 18 null null WellCompletion/New/Production or Monitoring/NA 953646 null null 921406 Injection Alameda County Water District 13 WCR2014-015309 null E0205117 null null -122.048878 Unknown null 05S 3/5/2014 NEWARK 18.1 INJ-B11 Alameda 02W Mount Diablo null NATIONAL E W P INC null 2 2.375 37.696685 null Unknown null null 01 DWR North Central Region Office null null null 7200 JOHNSON DRIVE 2015080 null null null null null WellCompletion/Destruction/NA/NA 695970 null null 941131119-1 Not Specified Zone 7 Water Agency - Alameda County Flood Control and Water Conservation District null WCR2015-010054 null E0275188 null null -121.917426 Unknown null 03S 7/15/2015 PLEASANTON 20 UST-1 Alameda 01W Mount Diablo null ENVIRONMENTAL CONTROL ASSOCIATES null 3 null 37.4315 Completeness Review - Auto-Complete - 06-JAN-20 null 6/21/2019 4 09 DWR North Central Region Office Direct Rotary null GPM 22148 Eden Canyon RD w2019-0491 null null 840 null 600 WellCompletion/New/Production or Monitoring/NA 510952 Bentonite Air Lift null Water Supply Domestic Alameda County Public Works Agency, Water Resources Section 600 WCR2019-015599 840 null null null -122.08 null WGS84 06S 10/22/2019 Castro Valley 840 2 Alameda 02W Mount Diablo 11/1/2019 MARTELL WATER SYSTEMS INC 1 4 null 37.7822890 Completeness Review - Auto-Complete - 12-NOV-18 10 Ft 7/13/2018 null 06 DWR North Central Region Office Other Hollow-stem Auger null null 2301 E 23rd AVE W2018-0633 null NAVD88 20 21.40 null WellCompletion/New/Production or Monitoring/NA 484288 Bentonite null 19-102-1-1 Monitoring Alameda County Public Works Agency, Water Resources Section 5 WCR2018-007848 20.0 null Surveyed 0.1 Ft -122.2368998 Other WGS84 02S 7/18/2018 Oakland 20 EW-1A Alameda 03W Mount Diablo 9/7/2018 EXPLORATION GEOSERVICES INC null 5 null 37.57119 null Centroid of Section null null 21 DWR North Central Region Office null null null null null null null null null null WellCompletion/New/Production or Monitoring/NA null null null null null Alameda County Water District null WCR0120609 null ACWD1792 null null -121.97812 Derived from TRS null 04S null null null null Alameda 01W Mount Diablo null null null 57 null 37.6769888 Completeness Review - Auto-Complete - 05-AUG-19 0.1 Ft 4/29/2019 null 13 DWR North Central Region Office null null null 1436 Grant AVE W2019-0308 null NAVD88 null 18.54 6.85 WellCompletion/Destruction/NA/NA 1046151 null null 411-039-001 Remediation Alameda County Public Works Agency, Water Resources Section null W

In [0]:
pd_df_shortage = df_shortage.toPandas()

In [0]:
# create pandas dataframe
pd_df_station = pd.DataFrame(data=data_stations)
df_station=spark.createDataFrame(pd_df_station)

perm_table_name = "table_station"
df_station.write.format("parquet").saveAsTable(f"MILESTONE2WATER.{perm_table_name}") 


In [0]:
# create pandas dataframe from JSON DATA
pd_df_groundwater = pd.DataFrame(data=data_groundwater)
df_groundwater=spark.createDataFrame(pd_df_groundwater)

perm_table_name = "table_groundwater"
df_groundwater.write.format("parquet").saveAsTable(f"MILESTONE2WATER.{perm_table_name}") 

In [0]:
%sql 
show tables in MILESTONE2WATER;

database tableName isTemporary milestone2water table_completion false milestone2water table_groundwater false milestone2water table_shortage false milestone2water table_station false

In [0]:
%sql 
select "Well Completion Count" as Table_Name, count(1) as Row_Count from milestone2water.table_completion
union
select "Ground Water Count" as Table_Name, count(1) as Row_Count from milestone2water.table_groundwater
union
select "Household Shortage Count" as Table_Name, count(1) as Row_Count from milestone2water.table_shortage
union
select "Station Count" as Table_Name, count(1) as Row_Count from milestone2water.table_station




Table_Name Row_Count Well Completion Count 1043032 Ground Water Count 2530751 Household Shortage Count 3774 Station Count 45922

In [0]:
%sql 
select  count(1) as row_count  from milestone2water.table_completion



row_count 1043032

In [0]:
df_station.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/Station.csv")

In [0]:
#df_groundwater.coalesce(1).write.format("com.databricks.spark.csv").option("header", "true").save("dbfs:/FileStore/WaterWell/groundwater.csv")



--------------------------------------------------------------------------- 
 NameError Traceback (most recent call last)
 <command-3550016270225479> in <module> 
 2 df_groundwater . coalesce ( 1 ) . write . format ( "com.databricks.spark.csv" ) . option ( "header" , "true" ) . save ( "dbfs:/FileStore/WaterWell/groundwater.csv" ) 
 3 
 ----> 4 df_wellcompletion . coalesce ( 1 ) . write . format ( "com.databricks.spark.csv" ) . option ( "header" , "true" ) . save ( "dbfs:/FileStore/WaterWell/wellcompletion.csv" ) 
 5 df_shortage . coalesce ( 1 ) . write . format ( "com.databricks.spark.csv" ) . option ( "header" , "true" ) . save ( "dbfs:/FileStore/WaterWell/shortage.csv" ) 

 NameError : name 'df_wellcompletion' is not defined

In [0]:

dbutils.fs.ls(f"dbfs:/FileStore/WaterWell/groundwater.csv")

Out[33]: [FileInfo(path='dbfs:/FileStore/WaterWell/groundwater.csv/_SUCCESS', name='_SUCCESS', size=0),
 FileInfo(path='dbfs:/FileStore/WaterWell/groundwater.csv/_committed_755157886083895489', name='_committed_755157886083895489', size=111),
 FileInfo(path='dbfs:/FileStore/WaterWell/groundwater.csv/_started_755157886083895489', name='_started_755157886083895489', size=0),
 FileInfo(path='dbfs:/FileStore/WaterWell/groundwater.csv/part-00000-tid-755157886083895489-6b6aa279-6254-4e87-8d86-bdd5c4ae25df-55-1-c000.csv', name='part-00000-tid-755157886083895489-6b6aa279-6254-4e87-8d86-bdd5c4ae25df-55-1-c000.csv', size=536304885)]

In [0]:
df_wellcompletion = spark.sql("SELECT * FROM  milestone2water.table_completion")

In [0]:
df_shortage = spark.sql("SELECT * FROM  milestone2water.table_shortage")

In [0]:
df_shortage.count()

Out[38]: 3774

- https://adb-8268979028189023.3.azuredatabricks.net/?o=826897902818902

- https://adb-8268979028189023.3.azuredatabricks.net/files/WaterWell/groundwater.csv/?o=8268979028189023



- https://adb-8268979028189023.3.azuredatabricks.net/files/WaterWell/groundwater.csv//part-00000-tid-755157886083895489-6b6aa279-6254-4e87-8d86-bdd5c4ae25df-55-1-c000.csv?o=8268979028189023

- https://adb-8268979028189023.3.azuredatabricks.net/files/WaterWell/Station.csv/part-00000-tid-8175063190170722800-757a8275-cd4b-40fb-a8d0-cd4e6697a20a-54-1-c000.csv?o=8268979028189023


- https://adb-8268979028189023.3.azuredatabricks.net/files/WaterWell/wellcompletion.csv/part-00000-tid-461276457967221884-5f4b19f1-0f0e-4a78-a13a-66ff90a9b027-66-1-c000.csv?o=8268979028189023

- https://adb-8268979028189023.3.azuredatabricks.net/files/WaterWell/shortage.csv/part-00000-tid-347414376517014295-70b4847f-5ffa-4c79-b389-736a993b950a-67-1-c000.csv?o=8268979028189023




#### Non-parquet files

- https://adb-8268979028189023.3.azuredatabricks.net/files/shortage.csv?o=8268979028189023
- https://adb-8268979028189023.3.azuredatabricks.net/files/wellcompletion.csv?o=8268979028189023
- https://adb-8268979028189023.3.azuredatabricks.net/files/groundwater.csv?o=8268979028189023

In [0]:
%sql

--select * from milestone2water.table_shortage

Well_Depth StatusType Status Household_Support Pump_Rate_Reduction Water_Issues Shortage_Type Was_Issue_Resolved? CREATE_DATE Approximate_Issue_Start_Date Measure_Date Primary_Usages Region LONGITUDE Well_to_Water_Depth ID CITY Approximate_Repair_Cost County Report_Date LATITUDE _id Additional_Info null Outage Undefined null null Well is dry (no longer producing water)
 Dry well (groundwater) null 05/24/2021 04/06/2021 null Household Southern -120.61821 null 10230 TEMPLETON null San Luis Obispo 2021-05-24T00:00:00 35.50495 2830 null 166 Resolved Interim Solution owner-occupied Yes, about a 30-40% reduction Reduction in water pressure, lower flows.
 Dry well (groundwater) No, trucking in water
 05/25/2021 05/04/2021 05/18/2021 Household Inland -119.78637 148 10247 Lemoore null Kings 2021-05-25T00:00:00 36.30101 2831 null 200 Resolved Interim Solution owner-occupied It's no longer producing any water Well is dry (no longer producing water)
 Dry well (groundwater) No, trucking in water
 05/25/2021 05/14/2021 05/20/2021 Household Inland -119.995 200 10248 Madera null Madera 2021-05-25T00:00:00 37.05132 2832 null null Resolved Interim Solution owner-occupied It's no longer producing any water Well is dry (no longer producing water)
 Dry well (groundwater) No, trucking in water
 05/26/2021 05/21/2021 05/25/2021 Household Inland -120.14357 0 10267 Madera null Madera 2021-05-26T00:00:00 37.01731 2833 null 200 Resolved Interim Solution owner-occupied It's no longer producing any water Well is dry (no longer producing water)
 Dry well (groundwater) No, trucking in water
 05/26/2021 05/24/2021 05/24/2021 Household Inland -120.328507 195 10268 Chowchilla null Madera 2021-05-26T00:00:00 37.020235 2834 null 117 Resolved Resolved owner-occupied too low to get accurate reading Reduction in water pressure, lower flows.
,Well is catching air, have to wait to be able to pump.
 Dry well (groundwater) Yes, lowered the pump bowl
,No, cannot afford to finance solutions.
 05/30/2021 08/15/2015 11/18/1977 Household Inland -122.18107 93 ft. 10287 corning null Tehama 2021-05-30T00:00:00 39.94158 2835 My wife and I are over 70 and enjoy gardening as a supplement to store bought we have one small garden (10 by 4) but would like to expand but with our water situation it's not possible. I am afraid one day the water level will drop below our pump and stay there. I don't know why our neighbor is not experiencing the same problems, different depth? different strata? 53' Resolved Interim Solution owner-occupied null Well is dry (no longer producing water)
 Dry well (groundwater) No, trucking in water
 05/31/2021 05/30/2021 null Household Inland -122.21164 null 10307 Orland null Glenn 2021-05-31T00:00:00 39.74636 2836 null 75 Outage Outage owner-occupied 85% reduction Reduction in water pressure, lower flows.
,Reduction in water quality
,Well is catching air, have to wait to be able to pump.
,Well is pumping sand, muddy water.
 Dry well (groundwater) Yes, lowered the pump bowl
,Pump burned up and have one on order and waiting to have a service company install it 
,No, cannot afford to finance solutions.
,No, getting water from our neighbors with a hose
 05/31/2021 05/01/2021 null Household Inland -122.15781 55 10308 Orland Dropping pump $500, new pump $1000. To start Glenn 2021-05-31T00:00:00 39.73126 2837 Everyone around us and neighbors are having the same problems and with our water table being so low we will have to drill the well deeper but the wait list in Orland and Glenn County is months out and we cannot afford that cost. null Resolved Interim Solution renter-occupied null Well is dry (no longer producing water)
 Dry well (groundwater) No, trucking in water
 06/01/2021 05/21/2021 null Household Inland -122.11097 null 10309 Orland null Glenn 2021-06-01T00:00:00 39.70626 2838 Family of 5 being evicted due to well running dry. No available housing for family of 5 nearby. 330 Outage Outage owner-occupied Not sure Well is catching a

In [0]:

spark_df_shortage = spark.sql("""select * from milestone2water.table_shortage """)

<a style='text-decoration:none;line-height:16px;display:flex;color:#5B5B62;padding:10px;justify-content:end;' href='https://deepnote.com?utm_source=created-in-deepnote-cell&projectId=b042e2da-6536-449d-95b8-d85fa08825de' target="_blank">
 </img>
Created in <span style='font-weight:600;margin-left:4px;'>Deepnote</span></a>